In [500]:
import torch
import torch.nn as nn
import numpy as np 
import matplotlib.pyplot as plt
from tqdm import tqdm
import os
import gymnasium as gym
import json

In [501]:
class DQN(torch.nn.Module):
    def __init__(self, n_states,n_actions,n_hidden_units):
        super(DQN, self).__init__()
        self.state_dim = n_states
        self.num_hidden_units = n_hidden_units
        
        self.num_actions = n_actions
        self.layer1 = torch.nn.Linear(self.state_dim, self.num_hidden_units)
        self.layer2 = torch.nn.Linear(self.num_hidden_units,self.num_hidden_units)
        self.layer3 = torch.nn.Linear(self.num_hidden_units, self.num_actions)
        self.dropout = torch.nn.Dropout(p=0.2)
        self.layer_norm = torch.nn.LayerNorm(self.num_hidden_units)
        self.relu = torch.nn.ReLU()

    # Called with either one element to determine next action, or a batch
    # during optimization. Returns tensor([[left0exp,right0exp]...]).
    def forward(self, x):
        x = self.layer1(x)
        #x = self.dropout(x)
        #x = self.layer_norm(x)
        x = self.relu(x)
        x = self.layer2(x)
        #x = self.dropout(x)
        #x = self.layer_norm(x)
        x = self.relu(x)
        x = self.layer3(x)
        return x

In [502]:
def buffer_to_JSON(replay_buffer,buffer_size):
    # Experience Replay stores transitions as numpy arrays for performance reasons
    # Need to transform this to a list in order to write properly to JSON
    """ Transforms replay buffer data to JSON data type
    """
    j = []
    for i in range(buffer_size):
        transition = {
            "state":replay_buffer.states[i].tolist(),
            "action":int(replay_buffer.actions[i]),
            "reward":float(replay_buffer.rewards[i]),
            "terminal":int(replay_buffer.terminals[i]),
            "next_state":replay_buffer.next_states[i].tolist()
        }
        j.append(transition)
    return j

def json_to_buffer(json_data,replay_buffer):
    """ Transfers JSON data to replay buffer directly
    """
    assert len(json_data)<=replay_buffer.max_size
    for i,j in enumerate(json_data):
        state = j["state"]
        action = j["action"]
        reward = j["reward"]
        terminal = j["terminal"]
        next_state=j["next_state"]
        replay_buffer.states[i] = state[0]
        replay_buffer.actions[i] = action
        replay_buffer.rewards[i] = reward
        replay_buffer.terminals[i] = terminal
        replay_buffer.next_states[i] = next_state[0]
    return len(json_data)
    
def save_json(path, data):
    """save json data
    Args:
        path (Path): path to json file
        data (dict): data to be saved in json file
    """
    with open(path,"w") as f:
        json.dump(data,f,indent=2)

def read_json(path):
    """read json file for stored ReplayBuffer data
    Args:
        path (path): path to json file
    Returns:
        data (list): data to be used for Expereince Replay
    """
    f = open(path)
    json_data = json.load(f)
    return json_data


In [503]:
class ReplayBuffer:
    def __init__(self, buffer_size, minibatch_size, observation_size):
        #self.buffer = []
        self.minibatch_size = minibatch_size
        #random.seed(seed)
        self.max_size = buffer_size
        self.pos = 0
        self.full = False
        self.states = np.zeros((self.max_size,observation_size))
        self.next_states = np.zeros((self.max_size,observation_size))
        self.actions = np.zeros(self.max_size,dtype=np.int8)
        self.rewards = np.zeros(self.max_size)
        self.terminals = np.zeros(self.max_size,dtype=np.int8)
        self.rand_generator = np.random.RandomState()

    def set_seed(self,seed=1):
        self.rand_generator = np.random.RandomState(seed)


    def append(self, state, action, reward, terminal, next_state):
        """
        Args:
            state (Numpy array): The state.              
            action (integer): The action.
            reward (float): The reward.
            terminal (integer): 1 if the next state is a terminal state and 0 otherwise.
            next_state (Numpy array): The next state.           
        """
        self.states[self.pos] = state
        self.actions[self.pos] = action
        self.rewards[self.pos] = reward
        self.terminals[self.pos] = terminal
        self.next_states[self.pos] = next_state
        self.pos += 1
        if(self.pos==self.max_size):
            self.pos = 0
            self.full = True


    def sample(self):
        """
        Returns:
            A list of transition tuples including state, action, reward, terinal, and next_state
        """
        if(self.full):
            idxs = self.rand_generator.randint(0,self.max_size,size=self.minibatch_size) 
        else:
            idxs = self.rand_generator.randint(0,self.pos,size=self.minibatch_size)
        sample_ = [self.states[idxs],self.actions[idxs],self.rewards[idxs],self.terminals[idxs],
                   self.next_states[idxs]]
        #print(sample_)
        return sample_

    def size(self):
        if(self.full):
            return self.max_size
        else:
            return self.pos
        
    def save_buffer(self,path="ReplayBuffer.JSON"):
        json_data = buffer_to_JSON(self,self.size())
        save_json(path,json_data)

    def load_buffer(self,path="ReplayBuffer.JSON"):
        self.reset()
        json_data = read_json(path)
        data_size=json_to_buffer(json_data,self)
        if(data_size==self.max_size):
            self.full = True
            self.pos = 0
        else:
            self.pos = data_size
        
    
    def reset(self):
        self.full = False
        self.pos = 0

In [504]:
def get_td_error(states, next_states, actions, rewards, discount, terminals, target_network, current_q_network):
    with torch.no_grad():
        # The idea of Double DQN is to get max actions from current network
        # and to get Q values from target_network for next states. 
        q_next_mat = current_q_network(next_states)
        max_actions = torch.argmax(q_next_mat,1)
        double_q_mat = target_network(next_states)
    batch_indices = torch.arange(q_next_mat.shape[0])
    double_q_max = double_q_mat[batch_indices,max_actions]
    target_vec = rewards+discount*double_q_max*(torch.ones_like(terminals)-terminals)
    q_mat = current_q_network(states)
    batch_indices = torch.arange(q_mat.shape[0])
    q_vec = q_mat[batch_indices,actions]
    #delta_vec = target_vec - q_vec
    return target_vec,q_vec

In [505]:
def optimize_network(experiences, discount, optimizer, target_network, current_q_network,device):
    """
    Args:
        experiences (Numpy array): The batch of experiences including the states, actions,
                                   rewards, terminals, and next_states.
        discount (float): The discount factor.
        network (ActionValueNetwork): The latest state of the network that is getting replay updates.
        current_q (ActionValueNetwork): The fixed network used for computing the targets,
                                        and particularly, the action-values at the next-states.
    """
    # Get states, action, rewards, terminals, and next_states from experiences
    states = experiences[0]
    actions = experiences[1]
    rewards = experiences[2]
    terminals = experiences[3]
    next_states = experiences[4]
    # numpy arrays to tensors and move to device (cpu or gpu)
    states = torch.tensor(states,dtype=torch.float32,device=device)
    next_states = torch.tensor(next_states,dtype=torch.float32,device=device)
    rewards = torch.tensor(rewards,dtype=torch.float32,device=device)
    terminals = torch.tensor(terminals,dtype=torch.int,device=device)
    actions = torch.tensor(actions,dtype=torch.int,device=device)
 
    # Compute TD error using the get_td_error function
    # Note that q_vec is a 1D array of shape (batch_size)
    target_vec,q_vec = get_td_error(states, next_states, actions, rewards, discount, terminals, target_network, current_q_network)
    loss_fun = torch.nn.MSELoss()
    loss = loss_fun(target_vec,q_vec)
    optimizer.zero_grad()
    loss.backward()
    torch.nn.utils.clip_grad_norm_(current_q_network.parameters(), 10)
    optimizer.step()
    return loss.detach().cpu().numpy()

In [506]:
class DQNAgent:
    def __init__(self,buffer_config):
        self.name = "DQN"
        self.device = None
        self.rand_generator = np.random.RandomState() # random seed. Later can be changed by using set_seed method
        self.replay_buffer = ReplayBuffer(buffer_config["replay_buffer_size"],
                                          buffer_config["minibatch_sz"],
                                          buffer_config["observation_size"])

    def set_seed(self,seed=1):
        self.rand_generator = np.random.RandomState(seed)
        #random.seed(self.seed)
    
    def set_epsilon_decay(self,n_steps=10000):
        self.eps_decay = 1. - 1./n_steps

    def set_device(self,device="cpu"):
        if(device=="cuda"):
            self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        else:
            self.device = torch.device("cpu")
    
    def agent_init(self, agent_config):
        if(self.device==None):
            device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        
        self.state_dim = agent_config["network_config"].get("state_dim")
        self.num_hidden_layers = agent_config["network_config"].get("num_hidden_units")
        self.num_actions = agent_config["network_config"].get("num_actions")
        
        self.network_type = agent_config["network_config"].get("network_type")
        
        self.q_network = DQN(self.state_dim,self.num_actions,self.num_hidden_layers).to(self.device)
        self.target_network = DQN(self.state_dim,self.num_actions,self.num_hidden_layers).to(self.device)
        self.target_network.load_state_dict(self.q_network.state_dict())
        
        self.step_size = agent_config['step_size']
        self.double_dqn = agent_config['double_dqn']
        self.num_actions = agent_config['network_config']['num_actions']
        self.num_replay = agent_config['num_replay_updates_per_step']
        self.discount = agent_config['gamma']
        self.epsilon = agent_config['epsilon']
        self.time_step = 0
        self.update_freq = agent_config['update_freq']
        self.loss = []
        self.episode_rewards = []
        self.loss_capacity = 5_000
        self.warmup_steps = agent_config['warmup_steps']
        self.eps_decay = 0.9999
        self.last_state = None
        self.last_action = None
        self.sum_rewards = 0
        self.episode_steps = 0
        self.optimizer = torch.optim.Adam(self.q_network.parameters(),lr=self.step_size,weight_decay=0.01)
        self.soft_update = True
        self.tau = 0.005

    def greedy_policy(self,state,epsilon=0.001):
        state = torch.tensor(state,dtype=torch.float32,device=self.device)
        a = self.rand_generator.rand()
        if(a>=epsilon):
            with torch.no_grad():
                action_values = self.q_network(state)
            action = torch.argmax(action_values).item()
        else:
            action = self.rand_generator.choice(self.num_actions)
        return action

    def epsilon_greedy_policy(self,state):
        epsilon = np.max([self.epsilon,0.05]) 
        state = torch.tensor(state,dtype=torch.float32,requires_grad=False,device=self.device)
        self.epsilon *= self.eps_decay
        a = self.rand_generator.rand()
        if(a>=epsilon):
            with torch.no_grad():
                action_values = self.q_network(state)
            action = torch.argmax(action_values).item()
        else:
            action = self.rand_generator.choice(self.num_actions)
        return action

    # Work Required: No.
    def agent_start(self, state):
        """The first method called when the experiment starts, called after
        the environment starts.
        Args:
            state (Numpy array): the state from the
                environment's evn_start function.
        Returns:
            The first action the agent takes.
        """
        self.sum_rewards = 0
        self.episode_steps = 0
        self.last_state = state #torch.tensor(np.array([state]),dtype=torch.float32,device=self.device)
        self.last_action = self.epsilon_greedy_policy(self.last_state)
        self.time_step += 1
        return self.last_action

    def agent_step(self, reward, state):
        """A step taken by the agent.
        Args:
            reward (float): the reward received for taking the last action taken
            state (Numpy array): the state from the
                environment's step based, where the agent ended up after the
                last step
        Returns:
            The action the agent is taking.
        """
        self.sum_rewards += reward
        self.episode_steps += 1
        #state = torch.tensor(np.array([state]),dtype=torch.float32,device=self.device)
        action = self.epsilon_greedy_policy(state)
        terminal = False
        self.replay_buffer.append(self.last_state, self.last_action, reward, terminal, state)

        # Perform replay steps:
        if self.replay_buffer.size() > self.replay_buffer.minibatch_size and self.time_step>self.warmup_steps: # and self.episode_steps%self.replay_buffer.minibatch_size==0:
            for _ in range(self.num_replay):
                # Get sample experiences from the replay buffer
                experiences = self.replay_buffer.sample()
                loss = optimize_network(experiences, self.discount, self.optimizer, self.target_network, self.q_network,self.device)
                if(len(self.loss)>=self.loss_capacity):
                    del self.loss[0]
                self.loss.append(loss)

        if(self.soft_update):
            self.polyak_update_target_network()
        else:
            if(self.time_step%self.update_freq==0):
                #print("Updating network")
                self.update_target_network()
       
        self.last_state = None
        self.last_action = None

        ### END CODE HERE
        # your code here
        self.last_state = state
        self.last_action = action
        self.time_step += 1
        return action

    def agent_end(self, reward):
        """Run when the agent terminates.
        Args:
            reward (float): the reward the agent received for entering the
                terminal state.
        """
        self.sum_rewards += reward
        self.episode_steps += 1
        self.episode_rewards.append(self.sum_rewards)
        # Set terminal state to an array of zeros
        state = np.zeros_like(self.last_state) #torch.zeros_like(self.last_state,device=self.device)

        # Append new experience to replay buffer
        # Note: look at the replay_buffer append function for the order of arguments
        end_loss = 0
        # your code here
        terminal = True
        self.replay_buffer.append(self.last_state, self.last_action, reward, terminal, state)
        # Perform replay steps:
        if self.replay_buffer.size() > self.replay_buffer.minibatch_size:
            for _ in range(self.num_replay):
                experiences = self.replay_buffer.sample()
                loss = optimize_network(experiences, self.discount, self.optimizer, self.target_network, self.q_network,self.device)
                end_loss = loss
                if(len(self.loss)>=self.loss_capacity):
                    del self.loss[0]
                self.loss.append(loss)
        
        if(self.soft_update):
            self.polyak_update_target_network()
        else:
            if(self.time_step%self.update_freq==0):
                #print("Updating network")
                self.update_target_network()
                
        self.time_step += 1
    
        return end_loss

    def agent_message(self, message):
        if message == "get_sum_reward":
            return self.sum_rewards
        else:
            raise Exception("Unrecognized Message!")
        
    def update_target_network(self):
        self.target_network.load_state_dict(self.q_network.state_dict())

    def polyak_update_target_network(self):
        one = torch.ones(1, requires_grad=False).to(self.device)
        for param, target_param in zip(self.q_network.parameters(), self.target_network.parameters()):
            target_param.data.mul_(1-self.tau)
            target_param.data.addcmul_(param.data, one, value=self.tau)

    def get_loss(self):
        return np.average(np.array(self.loss))

In [507]:
class offlineDQNAgent:
    def __init__(self,buffer_config):
        self.name = "offlineDQN"
        self.device = None
        self.rand_generator = np.random.RandomState() # random seed. Later can be changed by using set_seed method
        self.replay_buffer = ReplayBuffer(buffer_config["replay_buffer_size"],
                                          buffer_config["minibatch_sz"],
                                          buffer_config["observation_size"])
        self.buffer_path = "experienceReplay.json"

    def set_seed(self,seed=1):
        self.rand_generator = np.random.RandomState(seed)
        #random.seed(self.seed)
    
    def set_epsilon_decay(self,n_steps=10000):
        self.eps_decay = 1. - 1./n_steps

    def set_buffer_path(self,path="experienceReplay.json"):
        self.buffer_path = path
    
    def mean_loss(self):
        if(len(self.loss)==0):
            return -1
        else:
            loss = np.mean(self.loss)
            return loss

    def set_device(self,device="cpu"):
        if(device=="cuda"):
            self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        else:
            self.device = torch.device("cpu")
    
    def agent_init(self, agent_config):
        if(self.device==None):
            self.device = torch.device("cpu")

        self.state_dim = agent_config["network_config"].get("state_dim")
        self.num_hidden_layers = agent_config["network_config"].get("num_hidden_units")
        self.num_actions = agent_config["network_config"].get("num_actions")
        self.network_type = agent_config["network_config"].get("network_type")
        
        self.q_network = DQN(self.state_dim,self.num_actions,self.num_hidden_layers).to(self.device)
        self.target_network = DQN(self.state_dim,self.num_actions,self.num_hidden_layers).to(self.device)
        self.target_network.load_state_dict(self.q_network.state_dict())
        
        self.step_size = agent_config['step_size']
        self.num_actions = agent_config['network_config']['num_actions']
        self.num_replay = agent_config['num_replay_updates_per_step']
        self.discount = agent_config['gamma']
        
        self.time_step = 0
        
        self.loss = []
        self.episode_rewards = []
        self.loss_capacity = 5_000
        self.epsilon = agent_config['epsilon']
        self.time_step = 0
        self.update_freq = agent_config['update_freq']
    
        self.eps_decay = 0.9999
        self.last_state = None
        self.last_action = None
        self.sum_rewards = 0
        self.episode_steps = 0
        self.optimizer = torch.optim.Adam(self.q_network.parameters(),lr=self.step_size,weight_decay=0.01)
        self.tau = 0.005
        self.replay_buffer.load_buffer(self.buffer_path)

    def epsilon_greedy_policy(self,state):
        epsilon = np.max([self.epsilon,0.05]) 
        state = torch.tensor(state,dtype=torch.float32,requires_grad=False,device=self.device)
        self.epsilon *= self.eps_decay
        a = self.rand_generator.rand()
        if(a>=epsilon):
            with torch.no_grad():
                action_values = self.q_network(state)
            action = torch.argmax(action_values).item()
        else:
            action = self.rand_generator.choice(self.num_actions)
        return action

    def greedy_policy(self,state,epsilon=0.001):
        state = torch.tensor(state,dtype=torch.float32,device=self.device)
        a = self.rand_generator.rand()
        if(a>=epsilon):
            with torch.no_grad():
                action_values = self.q_network(state)
            action = torch.argmax(action_values).item()
        else:
            action = self.rand_generator.choice(self.num_actions)
        return action
    
    def load_buffer(self):
        self.replay_buffer.load_buffer()

    def learn_offline(self):
        self.episode_steps += 1
        # Perform replay steps:
        #if self.replay_buffer.size() > self.replay_buffer.minibatch_size and self.time_step>self.warmup_steps: # and self.episode_steps%self.replay_buffer.minibatch_size==0:
        for _ in range(self.num_replay):
            # Get sample experiences from the replay buffer
            experiences = self.replay_buffer.sample()
            #print(experiences)
            loss = optimize_network(experiences, self.discount, self.optimizer, self.target_network, self.q_network,self.device)
            if(len(self.loss)>=self.loss_capacity):
                del self.loss[0]
            self.loss.append(loss)
        self.update_target_network()

    # Work Required: No.
    def agent_start(self, state):
        """The first method called when the experiment starts, called after
        the environment starts.
        Args:
            state (Numpy array): the state from the
                environment's evn_start function.
        Returns:
            The first action the agent takes.
        """
        self.sum_rewards = 0
        self.episode_steps = 0
        self.last_state = state #torch.tensor(np.array([state]),dtype=torch.float32,device=self.device)
        self.last_action = self.epsilon_greedy_policy(self.last_state)
        self.time_step += 1
        return self.last_action

    def agent_step(self, reward, state):
        """A step taken by the agent.
        Args:
            reward (float): the reward received for taking the last action taken
            state (Numpy array): the state from the
                environment's step based, where the agent ended up after the
                last step
        Returns:
            The action the agent is taking.
        """
        self.sum_rewards += reward
        self.episode_steps += 1
        #state = torch.tensor(np.array([state]),dtype=torch.float32,device=self.device)
        action = self.epsilon_greedy_policy(state)
        terminal = False
        self.replay_buffer.append(self.last_state, self.last_action, reward, terminal, state)

        # Perform replay steps:
        if self.replay_buffer.size() > self.replay_buffer.minibatch_size: # and self.episode_steps%self.replay_buffer.minibatch_size==0:
            for _ in range(self.num_replay):
                # Get sample experiences from the replay buffer
                experiences = self.replay_buffer.sample()
                loss = optimize_network(experiences, self.discount, self.optimizer, self.target_network, self.q_network,self.device)
                if(len(self.loss)>=self.loss_capacity):
                    del self.loss[0]
                self.loss.append(loss)
            self.update_target_network()
       
        self.last_state = None
        self.last_action = None

        ### END CODE HERE
        # your code here
        self.last_state = state
        self.last_action = action
        self.time_step += 1
        return action

    def agent_end(self, reward):
        """Run when the agent terminates.
        Args:
            reward (float): the reward the agent received for entering the
                terminal state.
        """
        self.sum_rewards += reward
        self.episode_steps += 1
        self.episode_rewards.append(self.sum_rewards)
        # Set terminal state to an array of zeros
        state = np.zeros_like(self.last_state) #torch.zeros_like(self.last_state,device=self.device)

        # Append new experience to replay buffer
        # Note: look at the replay_buffer append function for the order of arguments
        end_loss = 0
        # your code here
        terminal = True
        self.replay_buffer.append(self.last_state, self.last_action, reward, terminal, state)
        # Perform replay steps:
        if self.replay_buffer.size() > self.replay_buffer.minibatch_size:
            for _ in range(self.num_replay):
                experiences = self.replay_buffer.sample()
                loss = optimize_network(experiences, self.discount, self.optimizer, self.target_network, self.q_network,self.device)
                end_loss = loss
                if(len(self.loss)>=self.loss_capacity):
                    del self.loss[0]
                self.loss.append(loss)
            self.update_target_network()
                
        self.time_step += 1
    
        return end_loss

    def update_target_network(self):
        one = torch.ones(1, requires_grad=False).to(self.device)
        for param, target_param in zip(self.q_network.parameters(), self.target_network.parameters()):
            target_param.data.mul_(1-self.tau)
            target_param.data.addcmul_(param.data, one, value=self.tau)

    def get_loss(self):
        return np.average(np.array(self.loss))

In [508]:
class RL:
    def __init__(self) -> None:
        self.name = "ButaChanRL"
        self.mean_episode_length = 0
        self.mean_episode_rew = 0
        self.mean_loss= 0
        self.step = 0
        self.output_step = 0
        self.epsiode_rewards = []
        self.episode_lens = []
        self.loss = []
        
        self.model_dir = "./models/"
        self.num_episodes = 0
        self.average_over = 20

    def set_output_step(self,output_step):
        self.output_step = output_step

    def set_model_dir(self,name):
        self.model_dir = name

    def create_model_dir(self):
        if not os.path.exists(self.model_dir):
            os.makedirs(self.model_dir)

    def load_model(self,model,filename="model.weights"):
        if(model.name == "DQN"):
            model.target_network.load_state_dict(torch.load(filename))
            model.q_network.load_state_dict(torch.load(filename))
        elif(model.name=="ActorCritic"):
            model.actor_critic_network.load_state_dict(torch.load(filename))
        else:
            NotImplementedError()

    def save_model(self,model,filename="model.weights"):
        if(model.name == "DQN"):
            torch.save(model.q_network.state_dict(),filename)
        elif(model.name=="ActorCritic"):
            torch.save(model.actor_critic_network.state_dict(),filename)
   
    def plot_live(self,data,n_mean=20,plot_start=20):
        plt.ion()
        plt.figure(1)
        plot_data = torch.tensor(data, dtype=torch.float,requires_grad=False)
        plt.clf()
        plt.title('Training...')
        plt.xlabel('Episode')
        plt.ylabel('Episode Reward')
        plt.plot(plot_data.numpy(),"o")
        # Take 100 episode averages and plot them too
        if len(plot_data ) >= plot_start:
            means = plot_data .unfold(0, n_mean, 1).mean(1).view(-1)
            means = torch.cat((torch.zeros(n_mean), means))
            plt.plot(means.numpy())
        plt.pause(0.1)  # pause a bit so that plots are updated

    def episode_summarize(self,episode,episode_reward):
        print(f"Episode: {episode}, Reward: {episode_reward}")

    def summarize(self):
        self.mean_episode_length = 0
        self.mean_episode_rew = 0
        if(len(self.episode_lens)>0):
            if(len(self.episode_lens)>self.average_over):
                self.mean_episode_length = np.average(self.episode_lens[-self.average_over:-1])
                self.mean_episode_rew = np.average(self.epsiode_rewards[-self.average_over:-1])
            else:
                self.mean_episode_length = np.average(self.episode_lens)
                self.mean_episode_rew = np.average(self.epsiode_rewards)
        self.mean_loss = 0
        if(len(self.loss)>0):
            self.mean_loss = np.average(self.loss)
        print(f"Step:{self.step}, Episode:{self.num_episodes} Mean_Epi_Len: {self.mean_episode_length:5.2f},Mean_Epi_Rew {self.mean_episode_rew:5.2f}, Loss: {self.mean_loss:5.2f}")

    def learn(self,agent,env,agent_parameters,NSTEPS=10000,visualize=False,output_step=1000,save_best_weights=False):
        epsiode = 1
        
        self.output_step = output_step
        # prepare agent
        agent.agent_init(agent_parameters)
        
        #agent.set_epsilon_decay(NSTEPS//2)
        state,info= env.reset() 
        #state = torch.tensor(state,dtype=torch.float32,device=agent.device)
        # choose initial action based on agent's results
        action = agent.agent_start(state)
        done = False
        epsiode_reward = 0
        episode_len = 0
        
        for i in tqdm(range(1,NSTEPS+1)):
            self.step = i
            #print(action)
            state,reward,terminated,truncated,info=env.step(action)
            #state = torch.tensor(state,dtype=torch.float32,device=agent.device)
            #state = torch.unsqueeze(state,0)
            #print(i,state,reward,action,done)
            epsiode_reward += reward
            done = terminated or truncated
            if(self.output_step>0 and self.step%self.output_step==0):
                self.summarize()
                #print(f"Epsilon {agent.epsilon:>5.3f}")
                if(visualize):
                    if(len(self.epsiode_rewards)>0):
                        self.plot_live(self.epsiode_rewards)
            if(done):
                loss = agent.agent_end(reward)
                #print("Loss length",len(agent.loss))
                self.loss.append(loss)
                
                if(save_best_weights):
                    self.create_model_dir()
                    if(len(self.epsiode_rewards)==0):
                        model_name = self.model_dir+f"model_{self.step}"
                        self.save_model(agent,model_name)
                    else:
                        if(epsiode_reward>max(self.epsiode_rewards)):
                            model_name = self.model_dir+f"model_{self.step}"
                            self.save_model(agent,model_name)
                self.epsiode_rewards.append(epsiode_reward)
                self.episode_lens.append(episode_len)
                epsiode += 1
                self.num_episodes += 1
                # restart next episode
                state,_= env.reset() 
                #state = torch.tensor(state,dtype=torch.float32,device=agent.device)
                #state = torch.unsqueeze(state,0)
                action = agent.agent_start(state)
                done = False
                epsiode_reward = 0
                episode_len = 0
            else:
                action = agent.agent_step(reward,state)
                episode_len+=1
        return agent
    
    def learn_offline(self,agent,agent_parameters,NSTEPS=10000,output_step=1000):
        self.output_step = output_step
        # prepare agent
        agent.agent_init(agent_parameters)
        for i in tqdm(range(1,NSTEPS+1)):
            agent.learn_offline()
            if(i%1000==0):
                print("Offline mean loss: ",agent.mean_loss())
        return agent
    

    def evaluate(self,agent,env,n_episodes=10,seed=1,visualize=False,eval_espilon=0.001):
        epsiode_rewards = []
        for episode in range(1,n_episodes+1):
            state,info = env.reset()
            #state = torch.tensor(state,dtype=torch.float32,device=agent.device)
            #state = torch.unsqueeze(state,0)
            #action = agent.greedy_policy(state,eval_espilon)
            action = agent.epsilon_greedy_policy(state)
            done = False
            epsiode_reward = 0
            episode_len = 0
            while not done:
                state,reward,terminated,truncated,info=env.step(action)
                #state = torch.tensor(state,dtype=torch.float32,device=agent.device)
                #state = torch.unsqueeze(state,0)
                epsiode_reward += reward
                done = terminated or truncated
                #action = agent.greedy_policy(state,eval_espilon)
                action = agent.epsilon_greedy_policy(state)
                episode_len += 1
            epsiode_rewards.append(epsiode_reward)
            self.episode_summarize(episode,epsiode_reward)
            #if(visualize):
            #    env.summarize()
        mean_rew = np.average(epsiode_rewards)
        std_rew = np.std(epsiode_rewards)
        return (mean_rew,std_rew) 

In [509]:
env = gym.make("CartPole-v1") # just create gym environment natively
torch.set_num_threads(1)  
n_state = env.observation_space.shape[0]
n_actions = env.action_space.n

agent_parameters = { # this is where you can choose neural networks adjust hyperparameters 
'network_config': {
    'state_dim': n_state,
    'num_hidden_units': 128,
    'num_actions': n_actions,
    "network_type":"dqn"
},
'replay_buffer_size': 1_000_000,
'minibatch_sz': 32,
'observation_size':n_state,
'num_replay_updates_per_step': 1,
"step_size": 3e-4,
'gamma': 0.99,
'epsilon': 1,
'update_freq':100,
'warmup_steps':1000,
'double_dqn':False
}
buffer_parameters = {
    "replay_buffer_size":1_000_000,
    "minibatch_sz":32,
    "observation_size":n_state
}
#agent = DQNAgent(buffer_parameters) # You can change to other agents such as SARSA, ActorCritic
agent = offlineDQNAgent(buffer_parameters)
agent.set_device(device="cpu")
rl = RL() # You need this to control the overall process of training
#s,_=env.reset(seed=1)
#agent.set_seed(1)
#agent.replay_buffer.set_seed(1)
agent.replay_buffer.load_buffer("replay_buffer_2024.json")
trained_agent = rl.learn_offline(agent,agent_parameters)
#print(agent.replay_buffer.size())
#trained_agent = rl.learn(agent,env,agent_parameters,NSTEPS=100_000,output_step=1000,visualize=True,save_best_weights=False) # training loop



  1%|          | 58/10000 [00:00<00:35, 283.83it/s]

[array([[-6.78643063e-02, -5.46489596e-01,  1.16474174e-01,
         9.90149319e-01],
       [ 3.35760787e-02, -2.89423149e-02,  3.26016955e-02,
        -3.27154584e-02],
       [-5.01716370e-03, -7.52492726e-01, -7.99900107e-03,
         8.44170332e-01],
       [ 4.08975855e-02, -1.70508832e-01, -8.06274489e-02,
         1.18869096e-01],
       [ 5.83583713e-02,  3.76314610e-01, -2.43161283e-02,
        -5.62329471e-01],
       [ 1.64453134e-01,  1.58360749e-01, -5.48701920e-03,
         1.02495849e-01],
       [-1.36812508e+00, -1.23909378e+00, -8.53576958e-02,
        -5.97624421e-01],
       [-8.91038775e-02, -1.63956061e-01,  5.82424849e-02,
         2.30030924e-01],
       [-3.27616513e-01, -8.83857310e-01, -8.37309435e-02,
         1.98153928e-01],
       [-9.05046821e-01, -9.47263062e-01, -1.19357176e-01,
        -2.06533801e-02],
       [-7.75983036e-02,  1.83490917e-01,  1.28075436e-01,
        -1.18117824e-01],
       [ 4.41548899e-02,  4.22282785e-01, -1.46427024e-02,
     

  1%|          | 116/10000 [00:00<00:34, 282.44it/s]

[array([[-4.26085927e-02, -2.20026851e-01,  2.06812825e-02,
         1.61469474e-01],
       [ 3.01708728e-02, -2.35834606e-02,  1.75795391e-01,
         7.21766949e-01],
       [ 3.36607080e-03,  2.22198740e-01, -2.72981767e-02,
        -2.65587598e-01],
       [-6.38523549e-02, -5.86713612e-01,  4.23819013e-02,
         6.66036725e-01],
       [-9.86942947e-02,  1.97804987e-01,  1.93910152e-01,
         4.92805392e-02],
       [-1.36812508e+00, -1.23909378e+00, -8.53576958e-02,
        -5.97624421e-01],
       [ 3.75481024e-02, -5.68697333e-01, -8.11452866e-02,
         5.84520340e-01],
       [-6.27690479e-02,  3.63030583e-01,  5.54154366e-02,
        -4.24542218e-01],
       [ 4.53649871e-02,  4.35001850e-01, -4.62013595e-02,
        -7.05429316e-01],
       [ 3.31267357e-01, -2.44471610e-01,  1.66949496e-01,
         1.04172027e+00],
       [ 6.20115362e-03, -1.96512774e-01, -1.01409573e-02,
         2.72022814e-01],
       [ 8.56432766e-02,  2.14509904e-01, -3.58040594e-02,
     

  2%|▏         | 175/10000 [00:00<00:34, 287.51it/s]

...

 12%|█▏        | 1212/10000 [00:04<00:35, 246.12it/s]

[array([[ 0.07093523,  0.36017972, -0.0577572 , -0.60365123],
       [ 0.01869283, -0.37566867, -0.03882695,  0.60444397],
       [ 0.09282617,  0.94785279, -0.19562647, -1.67390597],
       [ 0.41281712,  0.35783792, -0.13473155, -0.28464499],
       [-0.05411715, -1.19475377,  0.07261599,  1.7744931 ],
       [-0.02348893, -0.01407758,  0.02159508,  0.08852084],
       [-0.25953934,  0.59506619,  0.08924788, -0.94545943],
       [-0.49134716, -0.59563208,  0.01108522,  0.27198163],
       [ 0.08616608,  0.82930338, -0.1468567 , -1.35894978],
       [-0.03311731, -0.18203793,  0.02011599,  0.2095255 ],
       [-0.17385821, -0.54247069, -0.16040653, -0.20686674],
       [-0.28662741, -0.02804449,  0.03157505, -0.24051237],
       [ 0.48295811,  1.50595462, -0.14074035, -1.15502989],
       [ 0.09272627, -0.15651546, -0.0268963 ,  0.29782343],
       [ 0.21534956,  0.12718433,  0.04740179,  0.16900772],
       [-0.40961015, -1.1037482 , -0.02888833,  0.90379924],
       [ 0.0913215 ,  0

 12%|█▏        | 1244/10000 [00:04<00:33, 261.65it/s]

[array([[-3.54875374e-04,  5.65726161e-01, -7.08995163e-02,
        -6.88524663e-01],
       [ 1.39277387e+00,  3.31699640e-01,  1.44149929e-01,
         8.49931121e-01],
       [ 2.93689221e-01, -3.81554574e-01,  1.55202091e-01,
         4.31155145e-01],
       [-1.44011565e-02, -3.76984596e-01, -3.91874416e-03,
         4.98327672e-01],
       [-7.18676001e-02, -5.53223848e-01,  1.58709064e-01,
         1.09725749e+00],
       [-8.49345624e-02,  3.04984068e-03,  1.43719152e-01,
         5.34226537e-01],
       [ 1.62415151e-02, -5.26850581e-01, -1.22237355e-01,
         2.13517055e-01],
       [-6.82528913e-02, -2.45362774e-01,  1.33418679e-01,
         7.63013124e-01],
       [ 4.00509238e-01, -7.62097001e-01,  3.96491587e-02,
         7.98077345e-01],
       [ 3.22436206e-02,  3.88147295e-01, -2.04774383e-02,
        -5.86217821e-01],
       [ 5.60712740e-02,  1.99294388e-01, -1.13592893e-01,
        -4.76752400e-01],
       [-3.09381671e-02,  2.21829321e-02,  4.89093326e-02,
     

KeyboardInterrupt: 